In [89]:
# i am running this in google colab with the following versions :
!pip install ipyaggrid # Successfully installed ipyaggrid-0.5.4 jedi-0.19.1 simplejson-3.19.3

In [90]:
import os
import json
import numpy as np
import pandas as pd
import jinja2 as jj
import urllib.request as ur
from ipyaggrid import Grid

from google.colab import output
output.enable_custom_widget_manager()

In [91]:
url = 'https://raw.githubusercontent.com/widgetti/ipyaggrid/master/data/OlympicWinners.json'
with ur.urlopen(url) as res:
    data = json.loads(res.read().decode('utf-8'))
data = pd.DataFrame(data)
data.head()

athlete   age        country  year        date       sport  gold  \
0    Michael Phelps  23.0  United States  2008  24/08/2008    Swimming     8   
1    Michael Phelps  19.0  United States  2004  29/08/2004    Swimming     6   
2    Michael Phelps  27.0  United States  2012  12/08/2012    Swimming     4   
3  Natalie Coughlin  25.0  United States  2008  24/08/2008    Swimming     1   
4     Aleksey Nemov  24.0         Russia  2000  01/10/2000  Gymnastics     2   

   silver  bronze  total  
0       0       0      8  
1       0       2      8  
2       2       0      6  
3       2       3      6  
4       1       3      6

In [139]:
import ipywidgets as widgets
import datetime

#### Grid bug fixes:
# 1. ipyaggrid/ipyaggrid/grid.py : 241 should be 'range' not 'cols' ?
# 2. to_df['columns'] = pd.MultiIndex.from_tuples(*[data_up['index_columns']]) does not handle a corner case well and is copy-pasted about 5 times over
# 3. additional .get_selected_columns() after 'rows' . should be make this opt-in for backwards compatibility
# 4. broke the monolithic 'export' method in small pieces so it can be clearer what each piece does and can be overriden if need be
# 5. added grid_range_selection method for easy reacting to selections
def export_index(data_up, to_df):
  tmp1 = data_up['index_rows']['names']
  if len(tmp1)!=0:
    to_df['index'] = pd.MultiIndex.from_tuples(*[data_up['index_rows']['values']], names=tmp1)
  else:
    print ('!!! 0 index_rows:', tmp1)

def export_columns(data_up, to_df):
  i_col = data_up['index_columns']
  if len(i_col)==0:
    to_df['columns'] = []
  elif len(i_col[0]) == 1:
    to_df['columns'] = [elem[0] for elem in i_col]
  else:
    to_df['columns'] = pd.MultiIndex.from_tuples(i_col)


def export_per_key(self, key1, export_to_df) -> bool:
  data_up = self._grid_data_up.get(key1, None)
  if data_up is None:
    return False
  to_df = {}
  export_index(data_up, to_df)
  export_columns(data_up, to_df)
  to_df['data'] = data_up['data']

  df1 = pd.DataFrame(**to_df)
  if export_to_df:
    self.grid_data_out[key1] = df1
  else:
    self.grid_data_out[key1] = df1.to_dict(orient='records')
  return True


def export_all(self, change):
  if self.unsync: return

  if self.export_per_key('rows', self.export_to_df):
    # enableRangeSelection will trigger range and then a rows fire.
    # range will be _sometimes_ inaccurate of the mouse was clicked and dragged
    # we fire a columns export to get the actual selected columns
    self.get_selected_columns()

  self.export_per_key('grid', True)
  self.export_per_key('cols', self.export_to_df)
  self.export_per_key('range', self.export_to_df)
  self.grid_data_out = dict(counter = (self.grid_data_out.pop('counter', 0) +1), **self.grid_data_out)


Grid.export = export_all
Grid.export_per_key = export_per_key

#### Grid enhancements
def grid_range_selection(grid1, on_range_selection):
  grid1.export_mode = 'auto'
  grid1.last_selected_range = None
  def foo1(change):
    tmp1 = change.get('new', None)
    if tmp1!=None:
      on_range_selection(grid1)

  grid1.observe(foo1, 'grid_data_out')
  return grid1
Grid.grid_range_selection = grid_range_selection

In [130]:

def foo1(grid_options):
  out1 = widgets.Output()
  def display1(grid1):
    #if 'cols' in grid1._grid_data_up.keys(): # the fires will come in this order: range, rows, cols. So just listening to the last one only:
    if True:
      out1.clear_output()
      with out1:
        print (datetime.datetime.now(), grid1._grid_data_up.keys())
        if 'rows' in grid1.grid_data_out and 'cols' in grid1.grid_data_out:
          print ('rows & cols: ')
          display(grid1.grid_data_out['rows'][grid1.grid_data_out['cols'].columns.tolist()]) # this is a better 'range' but lets print out both
        if 'range' in grid1.grid_data_out:
          print ('range:')
          display(grid1.grid_data_out['range'])

  g1 = Grid(grid_data = data, grid_options=grid_options, theme='ag-theme-balham').grid_range_selection(display1)
  return widgets.VBox([g1, out1])

# plain case: no grouping, plain columns
columnDefs = [
    {'headerName': "Country", 'field': "country"},
    {'headerName': "Sport", 'field': "sport"},
    {'headerName': "Athlete", 'field': "athlete"},
    {'headerName': "Age", 'field': "age", 'aggFunc':'min'},
    {'headerName': "Total", 'field': "total", 'aggFunc':'sum'},
]
foo1({'columnDefs': columnDefs,'enableRangeSelection':True,'defaultColDef': {'sortable': 'true', 'filter': 'true', 'resizable': 'true'}})

In [133]:
# grouped table : only selecting leaf nodes works.
# Selecting Groups (such as Russia) or aggregated rows does not work! So pivot mode = True does not work as it shows only the aggregated rows.
columnDefs = [
    {'headerName': "Country", 'field': "country", 'rowGroup':True, 'hide':True},
    {'headerName': "Sport", 'field': "sport"},
    {'headerName': "Athlete", 'field': "athlete"},
    {'headerName': "Age", 'field': "age", 'aggFunc':'min'},
    {'headerName': "Total", 'field': "total", 'aggFunc':'sum'},
]
foo1({'columnDefs': columnDefs,'enableRangeSelection':True,'defaultColDef': {'sortable': 'true', 'filter': 'true', 'resizable': 'true'}})

In [135]:
# not grouped BUT with multi-index columns
# rows & columns is consistently better and never wrong. Range _sometimes_ does not update
columnDefs = [
    {'headerName': "Country", 'field': "country"},
    {'headerName': "Sport", 'field': "sport", },
    {'headerName': "Athlete", 'field': "athlete"},
    {'headerName': "Age", 'field': "age", 'aggFunc':'min'},
    {
        'headerName': "Results",
        'children': [
            {'headerName': "Total", 'field': 'total', 'columnGroupShow': 'closed', 'aggFunc':'sum'},
            {'headerName': "Gold", 'field': 'gold', 'columnGroupShow': 'open', 'aggFunc':'sum'},
            {'headerName': "Silver", 'field': 'silver', 'columnGroupShow': 'open', 'aggFunc':'sum'},
            {'headerName': "Bronze", 'field': 'bronze', 'columnGroupShow': 'open', 'aggFunc':'sum'}
        ]
    },
]
foo1({'columnDefs': columnDefs,'enableRangeSelection':True,'defaultColDef': {'sortable': 'true', 'filter': 'true', 'resizable': 'true'}})

Support for third party widgets will remain active for the duration of the session. To disable support:

In [137]:
# grouped AND with multi-index columns
columnDefs = [
    {'headerName': "Country", 'field': "country", 'rowGroup':True, 'hide':True},
    {'headerName': "Sport", 'field': "sport",},
    {'headerName': "Athlete", 'field': "athlete"},
    {'headerName': "Age", 'field': "age", 'aggFunc':'min'},
    {
        'headerName': "Results",
        'children': [
            {'headerName': "Total", 'field': 'total', 'columnGroupShow': 'closed', 'aggFunc':'sum'},
            {'headerName': "Gold", 'field': 'gold', 'columnGroupShow': 'open', 'aggFunc':'sum'},
            {'headerName': "Silver", 'field': 'silver', 'columnGroupShow': 'open', 'aggFunc':'sum'},
            {'headerName': "Bronze", 'field': 'bronze', 'columnGroupShow': 'open', 'aggFunc':'sum'}
        ]
    },
]
grid_options = {
    'columnDefs': columnDefs,
    'enableRangeSelection':True,
    'defaultColDef': {'sortable': 'true', 'filter': 'true', 'resizable': 'true'},
}
foo1({'columnDefs': columnDefs,'enableRangeSelection':True,'defaultColDef': {'sortable': 'true', 'filter': 'true', 'resizable': 'true'}})